# Setup

In [1]:
pip install nltk==3.4

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.4 MB 5.1 MB/s 
  Created wheel for nltk: filename=nltk-3.4-py3-none-any.whl size=1436399 sha256=3a3707c31c6a773007ff10cfc118beb4decb86cd0b6e3347d3e131d4f107deba
  Stored in directory: /root/.cache/pip/wheels/13/b8/81/2349be11dd144dc7b68ab983b58cd2fae353cdc50bbdeb09d0
Successfully built nltk
  Attempting uninstall: nltk
    Found existing installation: nltk 3.7
    Uninstalling nltk-3.7:
      Successfully uninstalled nltk-3.7


In [ ]:
import pandas
import nltk
nltk.download('punkt')
from nltk import word_tokenize
from nltk import everygrams
from nltk.util import ngrams

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
DB_Identifier = None
host_name = 'REDACTED'
db_username = 'REDACTED'
db_password = 'REDACTED'

In [ ]:
pip install PyMySql

In [ ]:
import pymysql
# db = pymysql.connect(host_name)
db = pymysql.connect(host=host_name,
                             user=db_username,
                             password=db_password,
                             database=DB_Identifier,
                             charset='utf8mb4',
                             cursorclass=pymysql.cursors.DictCursor)
print(db)

In [ ]:
cursor = db.cursor()
cursor

In [ ]:
# Gives us sql version
cursor.execute("select version()")

1

In [ ]:
data = cursor.fetchone()
print(data)
# Version: 8.0.23

{'version()': '8.0.27'}


# Creating and Connecting to DB

In [ ]:
sql = '''SHOW DATABASES'''
cursor.execute(sql)
for db in cursor.fetchall():
  print(db)

{'Database': 'JobInsights'}
{'Database': 'information_schema'}
{'Database': 'mysql'}
{'Database': 'performance_schema'}
{'Database': 'sys'}


In [ ]:
#cursor.execute("DROP DATABASE JobInsights")

In [ ]:
# Create Job-insight DB
# We first need to create a database
# sql = '''create database IF NOT EXISTS JobInsights'''
# cursor.execute(sql)

In [ ]:
# Check if it exists
sql = '''use JobInsights'''
cursor.execute(sql)

0

# Creating Tables for Companies and Postings

In [ ]:
# Postings Table
sql = '''
create table IF NOT EXISTS companies (
  company_id    INT NOT NULL AUTO_INCREMENT,
  company_name  VARCHAR(64),
  PRIMARY KEY   ( company_id )
)'''
cursor.execute(sql)

0

In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM companies'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'company_id', 'Type': 'int', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': 'auto_increment'}
{'Field': 'company_name', 'Type': 'varchar(64)', 'Null': 'YES', 'Key': '', 'Default': None, 'Extra': ''}


In [ ]:
# Postings Table
sql = '''
create table IF NOT EXISTS postings (
  posting_id    VARCHAR(56) UNIQUE NOT NULL,
  job_title     VARCHAR(128) NOT NULL,
  company_id    INT NOT NULL,
  job_description TEXT NOT NULL,
  cleaned_job_description TEXT,
  PRIMARY KEY   ( posting_id ),
  FOREIGN KEY   ( company_id ) REFERENCES companies (company_id) 
)'''
cursor.execute(sql)

0

In [ ]:
# Add the cleaned_job_description column
# This column will have the job description with:
#   1. Removed special characters
#   2. Lower case characters

#sql = 'ALTER TABLE postings ADD cleaned_job_description TEXT;'
#cursor.execute(sql)

In [ ]:
# Add the Date column
# This column will keep track of the time that postings are added

# sql = 'ALTER TABLE postings ADD date_scraped DATE;'
# cursor.execute(sql)

0

In [ ]:
# sql = """
#     UPDATE postings
#     SET date_scraped =
#     '2022-04-08'
# """
# cursor.execute(sql)
# cursor.execute("COMMIT")

0

In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM postings'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'posting_id', 'Type': 'varchar(56)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'job_title', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': '', 'Default': None, 'Extra': ''}
{'Field': 'company_id', 'Type': 'int', 'Null': 'NO', 'Key': 'MUL', 'Default': None, 'Extra': ''}
{'Field': 'job_description', 'Type': 'text', 'Null': 'NO', 'Key': '', 'Default': None, 'Extra': ''}
{'Field': 'cleaned_job_description', 'Type': 'text', 'Null': 'YES', 'Key': '', 'Default': None, 'Extra': ''}
{'Field': 'date_scraped', 'Type': 'date', 'Null': 'YES', 'Key': '', 'Default': None, 'Extra': ''}


In [ ]:
cursor.execute("SELECT date_scraped FROM postings")
for date in cursor.fetchall():
    print(date)

# Dummygram Table

In [ ]:
# Creating the Unigram Table
# Postings Table
sql = '''
create table IF NOT EXISTS dummygrams (
  dummygram         VARCHAR(128) NOT NULL,
  count             INT NOT NULL,
  PRIMARY KEY       ( dummygram )
)'''
cursor.execute(sql)

0

In [ ]:
cursor.execute("DROP TABLE dummygrams")

0

# Unigram table



In [ ]:
# Creating the Unigram Table
# Postings Table
sql = '''
create table IF NOT EXISTS unigrams (
  unigram           VARCHAR(128) NOT NULL,
  count             INT NOT NULL,
  PRIMARY KEY       ( unigram )
)'''
cursor.execute(sql)

0

In [ ]:
#sql ="ALTER TABLE unigrams_postings DROP PRIMARY KEY, ADD PRIMARY KEY (unigram, posting_id) "
#cursor.execute(sql)

In [ ]:
# Creating the Unigram_posting Table
# This is a table linking unigrams to the job postings they are found in
sql = '''
create table IF NOT EXISTS unigrams_postings (
  unigram       VARCHAR(128) NOT NULL,
  posting_id    VARCHAR(56) NOT NULL,
  PRIMARY KEY   ( unigram, posting_id ),
  FOREIGN KEY   ( unigram ) REFERENCES unigrams ( unigram ),
  FOREIGN KEY   ( posting_id ) REFERENCES postings ( posting_id )
)'''
cursor.execute(sql)

0

In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM unigrams'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'unigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'count', 'Type': 'int', 'Null': 'NO', 'Key': '', 'Default': None, 'Extra': ''}


In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM unigrams_postings'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'unigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'posting_id', 'Type': 'varchar(56)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}


# Bigram Table

In [ ]:
# Creating the Bigram Table
# Postings Table
sql = '''
create table IF NOT EXISTS bigrams (
  bigram            VARCHAR(128) NOT NULL,
  count             INT NOT NULL,
  PRIMARY KEY       ( bigram )
)'''
cursor.execute(sql)

0

In [ ]:
# Creating the Bigram_posting Table
# Postings Table
sql = '''
create table IF NOT EXISTS bigrams_postings (
  bigram        VARCHAR(128) NOT NULL,
  posting_id    VARCHAR(56) NOT NULL,
  PRIMARY KEY   ( bigram, posting_id ),
  FOREIGN KEY   ( bigram ) REFERENCES bigrams ( bigram ),
  FOREIGN KEY   ( posting_id ) REFERENCES postings ( posting_id )
)'''
cursor.execute(sql)

0

In [ ]:
# Creating the bigrams to unigrams table
sql = '''
create table IF NOT EXISTS bigrams_unigrams (
  bigram            VARCHAR(128) NOT NULL,
  unigram           VARCHAR(128) NOT NULL,
  PRIMARY KEY       ( bigram, unigram ),
  FOREIGN KEY       ( bigram ) REFERENCES bigrams ( bigram ),
  FOREIGN KEY       ( unigram ) REFERENCES unigrams ( unigram )
)'''
cursor.execute(sql)

0

In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM bigrams'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'bigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'count', 'Type': 'int', 'Null': 'NO', 'Key': '', 'Default': None, 'Extra': ''}


In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM bigrams_postings'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'bigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'posting_id', 'Type': 'varchar(56)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}


In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM bigrams_unigrams'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'bigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'unigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}


# Trigram Table

In [ ]:
# Creating the Bigram Table
# Postings Table
sql = '''
create table IF NOT EXISTS trigrams (
  trigram           VARCHAR(128) NOT NULL,
  count             INT NOT NULL,
  PRIMARY KEY       ( trigram )
)'''
cursor.execute(sql)

0

In [ ]:
# Creating the Bigram_posting Table
# Postings Table
sql = '''
create table IF NOT EXISTS trigrams_postings (
  trigram       VARCHAR(128) NOT NULL,
  posting_id    VARCHAR(56) NOT NULL,
  PRIMARY KEY   ( trigram, posting_id ),
  FOREIGN KEY   ( trigram ) REFERENCES trigrams ( trigram ),
  FOREIGN KEY   ( posting_id ) REFERENCES postings ( posting_id )
)'''
cursor.execute(sql)

0

In [ ]:
# Creating the Unigram Table
# Postings Table
sql = '''
create table IF NOT EXISTS trigrams_unigrams (
  trigram           VARCHAR(128) NOT NULL,
  unigram           VARCHAR(128) NOT NULL,
  PRIMARY KEY       ( trigram, unigram ),
  FOREIGN KEY       ( trigram ) REFERENCES trigrams ( trigram ),
  FOREIGN KEY       ( unigram ) REFERENCES unigrams ( unigram )
)'''
cursor.execute(sql)

0

In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM trigrams'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'trigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'count', 'Type': 'int', 'Null': 'NO', 'Key': '', 'Default': None, 'Extra': ''}


In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM trigrams_postings'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'trigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'posting_id', 'Type': 'varchar(56)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}


In [ ]:
# Test to see if Subreddits output properly
sql = 'SHOW COLUMNS FROM trigrams_unigrams'
cursor.execute(sql)
for field in cursor.fetchall():
  print(field)

{'Field': 'trigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}
{'Field': 'unigram', 'Type': 'varchar(128)', 'Null': 'NO', 'Key': 'PRI', 'Default': None, 'Extra': ''}


# Running Code

In [ ]:
cursor.execute("SELECT * FROM companies;")
temp = cursor.fetchall()
for line in temp:
    print(line)

In [ ]:
cursor.execute("SELECT * FROM postings;")
temp = cursor.fetchall()
for line in temp:
    print(line)

# Functions

## Clearing Tables

In [ ]:
# Removing Page ads
sql = """DELETE FROM unigrams_postings WHERE posting_id LIKE '%pagead%' """
cursor.execute(sql)
sql = """DELETE FROM postings WHERE posting_id LIKE '%pagead%' """
cursor.execute(sql)
cursor.execute("COMMIT")

0

In [ ]:
# Removing cmp
sql = """DELETE FROM unigrams_postings WHERE posting_id LIKE '%cmp=%' """
cursor.execute(sql)
sql = """DELETE FROM postings WHERE posting_id LIKE '%cmp=%' """
cursor.execute(sql)
cursor.execute("COMMIT")

0

In [ ]:
# Dropping from Unigrams
# sql = """DELETE FROM unigrams"""
# cursor.execute(sql)
# cursor.execute("COMMIT")

## Database Getters

In [ ]:
# Get postings
def get_postings():

    sql = "SELECT * FROM postings"
    cursor.execute(sql)

    return cursor.fetchall()

def get_posting_ids():
    sql = "SELECT posting_id FROM postings"
    cursor.execute(sql)

    return cursor.fetchall()

def get_job_titles():
    sql = "SELECT job_title FROM postings"
    cursor.execute(sql)

    return cursor.fetchall()

def get_company_ids():
    sql = "SELECT company_id FROM postings"
    cursor.execute(sql)

    return cursor.fetchall()

def get_job_descriptions():
    sql = "SELECT job_description FROM postings"
    cursor.execute(sql)

    return cursor.fetchall()

def get_cleaned_job_descriptions():
    sql = "SELECT cleaned_job_description FROM postings"
    cursor.execute(sql)

    return cursor.fetchall()

print(get_postings())
print(get_posting_ids())
print(get_job_titles())
print(get_company_ids())
print(get_job_descriptions())
print(get_cleaned_job_descriptions())

[{'posting_id': '/rc/clk?jk=002e791737ba9119&fccid=19fc110b71511ecb&vjs=3', 'job_title': 'Software Developer - Vapor/Swift/React', 'company_id': 374, 'job_description': '\n/responsibilities/', 'cleaned_job_description': 'responsibilities', 'date_scraped': datetime.date(2022, 4, 8)}, {'posting_id': '/rc/clk?jk=006d4e70e47a02e4&fccid=56c2878cd8ff3ddc&vjs=3', 'job_title': 'Junior Pen Tester', 'company_id': 76, 'job_description': '\n/skills/\n  Some experience with burpsuite\n  Understanding of web apps\n  TCP Networking exposure\n  Mobile app familiarity\n  1-3 years of experience in pentesting or a related discipline\n  Entry level pentesting certification\n\n', 'cleaned_job_description': 'skills some experience burpsuite understanding web apps tcp networking exposure mobile app familiarity 1 3 years experience pentesting or related discipline entry level pentesting certification', 'date_scraped': datetime.date(2022, 4, 8)}, {'posting_id': '/rc/clk?jk=013aa83b3f0d97fb&fccid=05466bf41499f

In [ ]:
# boolean checks

# If the select statements finds a value, then it returns 1
# We can use this to determine if an ngram exists
def is_in_unigrams(text):

    sql = "SELECT unigram from unigrams WHERE unigram = %s"
    value = (text,)
    return cursor.execute(sql,text)

def is_in_bigrams(text):

    sql = "SELECT bigram from bigrams WHERE bigram = %s"
    value = (text,)
    return cursor.execute(sql,text)

def is_in_trigrams(text):

    sql = "SELECT trigram from trigrams WHERE trigram = %s"
    value = (text,)
    return cursor.execute(sql,text)

print(is_in_unigrams("respond"))
print(is_in_unigrams("re3spond"))
print(is_in_bigrams("respond quickly"))
print(is_in_bigrams("respond quickl2y"))
print(is_in_trigrams("respond quickly asd"))
print(is_in_trigrams("respond quickl2y asd"))

1
0
1
0
0
0


In [ ]:
cleaned_jobs = get_cleaned_job_descriptions()

for i,u in enumerate(cleaned_jobs):
    print(u)

print(i)

{'cleaned_job_description': 'responsibilities'}
{'cleaned_job_description': 'skills some experience burpsuite understanding web apps tcp networking exposure mobile app familiarity 1 3 years experience pentesting or related discipline entry level pentesting certification'}
{'cleaned_job_description': 'qualifications bachelor degree from an accredited college or university minimum three 3 years relevant work experience equivalent training or experience may substituted degree requirement cisco certifications ccna microsoft network operating system certifications unix linux experience knowledge military radios satcom systems wireless technology 802 11 wireless mobile adhoc network technology travel is required 20 30 well some weekend offhours support subject government security investigation must meet eligibility requirements access classified information skills military background or familiarity military command control structures possess working knowledge organizational interface militar

## Clean job posting descriptions

In [ ]:
import re

def compress_whitespaces(text):

    compressed_text = re.sub('[ ]+', " ", text)
    return compressed_text

def remove_weird_chars(text):
    reduced_text = re.sub('ﬀ', "ff", text)
    return reduced_text
    
def remove_words(text):
    words_to_remove = ["and", "to", "of", "the", "with", "in", "for", "a", 
                       "as", "it", "on", "be", "'", "s", "such", "at",
                       "it's", "'s", "’", "by"]

    

    word_list = nltk.word_tokenize(text)

    filtered_words = []

    for word in word_list:
        if word not in words_to_remove:
            filtered_words.append(word)

    text = " ".join(filtered_words)
    text = compress_whitespaces(text)


    return text

def clean_job_desc(job_desc: str):
    # job_desc will be passed in

    # First replace all punctuation except ' with white space with regex
    job_desc = re.sub('[\\n/,.!@#$%^&*()\[\]_;:\"<>-]', " ", job_desc)
    #print(job_desc)

    # Compress all white spaces so that there are no repeats
    job_desc = compress_whitespaces(job_desc)

    job_desc = remove_weird_chars(job_desc)

    # Lowercase all the alpha characters
    job_desc = job_desc.lower()
    

    job_desc = remove_words(job_desc)
    #print(job_desc)

    return job_desc

## Add cleaned job description to postings

In [ ]:
# Clean it, then update that posting's cleaned job description
def update_cleaned_job_descriptions():
    # Iterate over every posting
    sql = "SELECT * FROM postings"
    cursor.execute(sql)

    for job in cursor.fetchall():

        # If there is no cleaned job description for that posting
        #if not job["cleaned_job_description"]:

        # if statement to update description anyways
        if True:

            # Grab the description
            curr_desc = job["job_description"]

            # Clean it
            cleaned_desc = clean_job_desc(curr_desc)

            # Check if the description looks alright
            # print(cleaned_desc)

            # Insert the cleaned desc into postings
            sql = "UPDATE postings SET cleaned_job_description = %s WHERE posting_id = %s"

            # posting_id is taken from the current job to
            # update that records cleaned_job_description
            values = (cleaned_desc, job["posting_id"])

            cursor.execute(sql, values)
            
            cursor.execute("COMMIT")

update_cleaned_job_descriptions()

In [ ]:
for i in get_cleaned_job_descriptions():
    print(i)

{'cleaned_job_description': 'responsibilities'}
{'cleaned_job_description': 'skills some experience burpsuite understanding web apps tcp networking exposure mobile app familiarity 1 3 years experience pentesting or related discipline entry level pentesting certification'}
{'cleaned_job_description': 'qualifications bachelor degree from an accredited college or university minimum three 3 years relevant work experience equivalent training or experience may substituted degree requirement cisco certifications ccna microsoft network operating system certifications unix linux experience knowledge military radios satcom systems wireless technology 802 11 wireless mobile adhoc network technology travel is required 20 30 well some weekend offhours support subject government security investigation must meet eligibility requirements access classified information skills military background or familiarity military command control structures possess working knowledge organizational interface militar

## Get Job postings tokens

In [ ]:
# data: a dictionary of the ngram as key and count as it's value
# ngram_type: unigram, bigram, or trigram
# target: Rows added each iteration
def fast_ngram_insert(data, ngram_type, target, debug = False):

    table_name = ngram_type + "s" # add s since table names end are plural
    # Add each ngram to it's respective table

    # We use string iterpolation with {} to easily add in the variable names
    sql_insert = f"""
    INSERT INTO {table_name}
        ({ngram_type}, count)
    VALUES
        """ # Don't include the first tuple

    sql_update = """ON DUPLICATE KEY UPDATE
                        count = VALUES(count)"""

    # Iterate over each unigram
    # Insert TARGET amount of rows at a time
    count = 0
    TARGET = target
    values = ()
    for key,value in data.items():
        
        # Increment count
        count += 1
        values += (key,value) # Add the new values
        sql_insert += "(%s, %s),"
        
        
        # Every 100 rows, reset the row count
        # Insert all the rows
        if count >= TARGET:
            count = 0

            # Cut off the comma at the end of the sql_insert
            final_sql = sql_insert[:-1] + " " + sql_update
        
            if debug:
                print(values)
                print(final_sql)
            cursor.execute(final_sql, values)

            # Reset the values and insert statement
            values = ()
            sql_insert = f"""
            INSERT INTO {table_name}
                ({ngram_type}, count)
            VALUES
                """
            cursor.execute("COMMIT")        


    # If values is empty then there are no remaining rows
    if values:
        # Some of the rows will not reach over to 100
        # Catch the leftovers out here
        # Cut off the comma at the end of the sql_insert
        final_sql = sql_insert[:-1] + " " + sql_update
        cursor.execute(final_sql, values)
        cursor.execute("COMMIT")

### Unigram Functions

In [ ]:
# Compare new data to previous
# New unigrams are inserted
# Old unigrams are updated
def update_unigrams():
    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()
    #print(job_descriptions[0]['job_description'])

    # Collect all the new unigram_data
    unigram_dict = {}

    # Iterate over all job descriptions and collect each unigram with it's frequency
    # Unigram-frequency mapping is in the unigram_dict
    for specific_description in job_descriptions:
        #print(specific_description)
        curr_description = specific_description['cleaned_job_description']

        if curr_description:
            token = nltk.word_tokenize(curr_description)

            fdistunigrams = nltk.FreqDist(token)
            for u in fdistunigrams.items():
                
                temp_word = u[0]
                word_count = u[1]

                if temp_word in unigram_dict:
                    unigram_dict[temp_word] += word_count
                else:
                    unigram_dict[temp_word] = word_count

    # Use fast ngram insert to insert all the new rows very fast
    fast_ngram_insert(unigram_dict, "unigram", 1000, True)

In [ ]:
# Depends on the unigram and postings existing
# This function can only run after update_unigrams
# If a unigram is found that does not exist in the unigrams table, then
# update unigram needs to be run again

# Output
# This code results in a link table that maps unigrams to the respective
# job postings they can be found in
def update_unigrams_postings():

    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()

    for specific_description in job_descriptions:
        #print(specific_description)
        curr_description = specific_description['cleaned_job_description']
        curr_posting_id = specific_description['posting_id']

        values = []
        sql = "INSERT IGNORE INTO unigrams_postings (unigram, posting_id) VALUES"

        # If the current description is not null
        if curr_description:
            print(curr_posting_id)
            token = nltk.word_tokenize(curr_description)

            # Get all the individual unigrams (tokens)
            fdistunigrams = nltk.FreqDist(token)
            for u in fdistunigrams.items():

                # Our current unigram
                temp_unigram = u[0]

                # If unigram is not in unigram set raise error
                if not is_in_unigrams(temp_unigram):
                    raise ValueError("Unigram", temp_unigram, "Not in unigrams table")

                #print(temp_unigram)

                # Get the current values and prepare the next input
                values += [temp_unigram, curr_posting_id]
                sql += "(%s, %s),"


            # Convert values to a tuple
            values = tuple(values)
            sql = sql[:-1]
                
            # If there are no new values skip
            if values:
                cursor.execute(sql,values)
            
            # Commit as we go in case there is an error
            cursor.execute("COMMIT")

In [ ]:
update_unigrams()

('responsibilities', 304, 'skills', 897, 'some', 21, 'experience', 1347, 'burpsuite', 1, 'understanding', 188, 'web', 214, 'apps', 2, 'tcp', 8, 'networking', 55, 'exposure', 23, 'mobile', 50, 'app', 10, 'familiarity', 102, '1', 76, '3', 88, 'years', 327, 'pentesting', 2, 'or', 1181, 'related', 272, 'discipline', 29, 'entry', 13, 'level', 115, 'certification', 36, 'qualifications', 392, 'bachelor', 171, 'degree', 270, 'from', 146, 'an', 264, 'accredited', 34, 'college', 28, 'university', 21, 'minimum', 80, 'three', 12, 'relevant', 73, 'work', 583, 'equivalent', 113, 'training', 62, 'may', 86, 'substituted', 4, 'requirement', 7, 'cisco', 6, 'certifications', 31, 'ccna', 2, 'microsoft', 95, 'network', 141, 'operating', 83, 'system', 191, 'unix', 19, 'linux', 47, 'knowledge', 569, 'military', 7, 'radios', 1, 'satcom', 1, 'systems', 408, 'wireless', 16, 'technology', 259, '802', 1, '11', 4, 'adhoc', 1, 'travel', 27, 'is', 293, 'required', 225, '20', 8, '30', 3, 'well', 115, 'weekend', 4, 'o

In [ ]:
update_unigrams_postings()

In [ ]:
sql = "SELECT * FROM unigrams ORDER BY count DESC"
cursor.execute(sql)

unigrams = cursor.fetchall()

for k in unigrams:
    print(k)
    
#unigram_list = list(unigrams)
#print(unigram_list)

Streaming output truncated to the last 5000 lines.
{'unigram': 'its', 'count': 26}
{'unigram': 'long', 'count': 26}
{'unigram': 'prior', 'count': 26}
{'unigram': 'recognized', 'count': 26}
{'unigram': 'small', 'count': 26}
{'unigram': 'they', 'count': 26}
{'unigram': 'tickets', 'count': 26}
{'unigram': 'upgrades', 'count': 26}
{'unigram': 'version', 'count': 26}
{'unigram': '4', 'count': 25}
{'unigram': 'also', 'count': 25}
{'unigram': 'applicable', 'count': 25}
{'unigram': 'deploy', 'count': 25}
{'unigram': 'develops', 'count': 25}
{'unigram': 'group', 'count': 25}
{'unigram': 'guidance', 'count': 25}
{'unigram': 'individual', 'count': 25}
{'unigram': 'interact', 'count': 25}
{'unigram': 'jira', 'count': 25}
{'unigram': 'master', 'count': 25}
{'unigram': 'node', 'count': 25}
{'unigram': 'privacy', 'count': 25}
{'unigram': 'scalable', 'count': 25}
{'unigram': 'schedule', 'count': 25}
{'unigram': 'servers', 'count': 25}
{'unigram': 'vendor', 'count': 25}
{'unigram': '365', 'count': 24}


In [ ]:
sql = "SELECT * FROM unigrams_postings"
cursor.execute(sql)

unigrams = cursor.fetchall()

for k in unigrams:
    print(k)

Streaming output truncated to the last 5000 lines.
{'unigram': 'oriented', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'possesses', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'problem', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'professional', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'programming', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'python', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'qualifications', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'reasoning', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'required', 'posting_id': '/rc/clk?jk=7631da235493340e&fccid=69721041e85636d8&vjs=3'}
{'unigram': 'ruby', 'posting_id': '/rc/clk?jk=7631da235

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



### Bigram Functions

In [ ]:
def update_bigrams():
    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()
    #print(job_descriptions[0]['job_description'])

    bigram_dict = {}

    # Iterate over all job descriptions and collect each unigram with it's frequency
    # Unigram-frequency mapping is in the unigram_dict
    for specific_description in job_descriptions:
        print(specific_description)
        curr_description = specific_description['cleaned_job_description']

        if curr_description:
            token = nltk.word_tokenize(curr_description)
            # Set up the bigram
            bigram_tokens = ngrams(token, 2)

            # Get all the individual bigrams (tokens)
            fdistbigrams = nltk.FreqDist(bigram_tokens)
            for u,n in fdistbigrams.items():
                
                temp_word = u[0] + " " + u[1]
                word_count = n

                print(temp_word)

                if temp_word in bigram_dict:
                    bigram_dict[temp_word] += word_count
                else:
                    bigram_dict[temp_word] = word_count

    fast_ngram_insert(bigram_dict, "bigram", 1000)

In [ ]:
# Depends on the bigrams and postings existing
# This function can only run after update_unigrams
# If a bigram is found that does not exist in the bigram table, then
# update bigram needs to be run again

# Output
# This code results in a link table that maps bigrams to the respective
# job postings they can be found in
def update_bigrams_postings():

    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()

    sql = "SELECT bigram from bigrams"
    cursor.execute(sql)
    bigram_list = cursor.fetchall()

    # Construct a bigrams set that keeps track of all existing unigrams
    bigrams_set = set()
    for bigrams in bigram_list:
        #print(unigrams)
        bigrams_set.add(bigrams['bigram'])

    for specific_description in job_descriptions:
        #print(specific_description)
        curr_description = specific_description['cleaned_job_description']
        curr_posting_id = specific_description['posting_id']

        values = []
        sql = "INSERT IGNORE INTO bigrams_postings (bigram, posting_id) VALUES"

        # If the current description is not null
        if curr_description:
            print(curr_description)
            token = nltk.word_tokenize(curr_description)

            # Set up the trigram
            trigram_tokens = ngrams(token, 2)

            # Get all the individual bigrams (tokens)
            fdistunigrams = nltk.FreqDist(trigram_tokens)
            for u,n in fdistunigrams.items():

                # Our current trigram
                temp_bigram = u[0] + " " + u[1]
                #print(temp_bigram)

                # If Bigram is not in Bigram table set raise error
                if not is_in_bigrams(temp_bigram):
                    raise ValueError("Bigram", temp_bigram, "Not in Bigram table")

                values += [temp_bigram, curr_posting_id]
                sql += "(%s, %s),"

            # Convert values to a tuple
            values = tuple(values)
            sql = sql[:-1]
            #print(values)
            #print(sql)
            
            if values:
                cursor.execute(sql,values)

                # Commit as we go in case there is an error
            cursor.execute("COMMIT")

In [ ]:
# Maps bigrams to the unigrams that make them up
def update_bigrams_unigrams():

    # Select the current set of bigrams
    sql = "SELECT bigram FROM bigrams"
    cursor.execute(sql)

    # Get the entire list of dicts
    bigram_list = cursor.fetchall()

    # Iterate over every dict
    for bigram in bigram_list:
        # Get the actual bigram from the dict
        # We need to keep track of the original string since
        # it is the primary key in the bigram table
        curr_bigram = bigram["bigram"]

        # Split the bigram on the space character
        split_bigram = curr_bigram.split(" ")

        # The first word in the bigram
        word_one = split_bigram[0]
        # the second word in the bigram
        word_two = split_bigram[1]

        # Insert into bigrams_unigrams two rows, one for each word in the bigram
        sql = """INSERT IGNORE INTO bigrams_unigrams 
                    (bigram, unigram)
                VALUES
                    (%s, %s),
                    (%s, %s)"""

        # The bigram is curr_bigram, the unigram is the current word
        # This method allows for two rows to be inserted at the same time
        values = (curr_bigram, word_one, curr_bigram, word_two)
        
        print(curr_bigram)

        cursor.execute(sql, values)
        cursor.execute("COMMIT")

In [ ]:
update_bigrams()

Streaming output truncated to the last 5000 lines.
projects like
like joomla
joomla drupal
drupal wikis
wikis oscommerce
oscommerce etc
etc experience
experience common
common third
third party
party apis
apis google
google facebook
facebook ebay
ebay etc
etc desire
desire develop
develop new
new bold
bold ideas
ideas while
while constantly
constantly following
following best
best design
design coding
coding practices
practices bs
bs or
or ms
ms degree
degree computer
computer science
science engineering
engineering or
or other
other related
related area
area knowledge
{'posting_id': '/rc/clk?jk=ed5f97694376c2a5&fccid=957bd03bc6212791&vjs=3', 'cleaned_job_description': 'responsibilities handling customer service queries via telephone resolve account billing payment update customers progress their query when first contact resolution is not liaise other departments where needed provide speedy quality resolution our manage customer complaints queries our ensure we meet our agreed customer

In [ ]:
update_bigrams_postings()

responsibilities
skills some experience burpsuite understanding web apps tcp networking exposure mobile app familiarity 1 3 years experience pentesting or related discipline entry level pentesting certification
qualifications bachelor degree from an accredited college or university minimum three 3 years relevant work experience equivalent training or experience may substituted degree requirement cisco certifications ccna microsoft network operating system certifications unix linux experience knowledge military radios satcom systems wireless technology 802 11 wireless mobile adhoc network technology travel is required 20 30 well some weekend offhours support subject government security investigation must meet eligibility requirements access classified information skills military background or familiarity military command control structures possess working knowledge organizational interface military federal state local agencies demonstrate time management problem solving skills self moti

In [ ]:
update_bigrams_unigrams()

Streaming output truncated to the last 5000 lines.
tasks problems
tasks procedures
tasks projects
tasks provide
tasks reasonable
tasks required
tasks resolving
tasks security
tasks simultaneously
tasks skills
tasks smaller
tasks software
tasks team
tasks that
tasks through
tasks toil
tasks which
tasks work
taught when
taught… skills
taxonomies visual
tcp ip
tcp networking
tdd automated
tdd concepts
tdd development
tdd static
teach coding
teach learn
teach this…
teach you
teachers understands
teaching college
teaching transferable
team ability
team able
team across
team advance
team advanced
team advancing
team agile
team all
team also
team an
team analyzing
team application
team assigned
team assignments
team authorized
team back
team being
team both
team bring
team build
team building
team business
team can
team capable
team centric
team cirt
team code
team collaborating
team collaboration
team collaborative
team communicate
team complete
team complex
team comprised
team continually
t

In [ ]:
sql = "SELECT * from bigrams"
cursor.execute(sql)

for bi in cursor.fetchall():
    print(bi)

In [ ]:
sql = "SELECT * from bigrams_postings"
cursor.execute(sql)

for bi in cursor.fetchall():
    print(bi)

In [ ]:
sql = "SELECT * from bigrams_unigrams"
cursor.execute(sql)

for bi in cursor.fetchall():
    print(bi)

### Trigram Functions

In [ ]:
def update_trigrams():
    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()

    trigram_dict = {}

    # Iterate over all job descriptions and collect each unigram with it's frequency
    # Trigram-frequency mapping is in the unigram_dict
    for specific_description in job_descriptions:
        curr_description = specific_description['cleaned_job_description']

        if curr_description:
            token = nltk.word_tokenize(curr_description)
            # Set up the bigram
            trigram_tokens = ngrams(token, 3)

            # Get all the individual bigrams (tokens)
            fdisttrigrams = nltk.FreqDist(trigram_tokens)
            for u,n in fdisttrigrams.items():
                
                # u is a tuple of 3 elements, each being a word of the trigram
                # Since u will contain 3 elements, we concatenate them together
                # to form the trigram
                temp_word = u[0] + " " + u[1] + " " + u[2]
                word_count = n # The final wordcount

                if temp_word in trigram_dict:
                    trigram_dict[temp_word] += word_count
                else:
                    trigram_dict[temp_word] = word_count
    
    fast_ngram_insert(trigram_dict, "trigram", 1000)

In [ ]:
# Depends on the trigrams and postings existing
# This function can only run after update_unigrams
# If a trigram is found that does not exist in the trigram table, then
# update trigram needs to be run again

# Output
# This code results in a link table that maps trigram to the respective
# job postings they can be found in
def update_trigrams_postings():

    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()

    for specific_description in job_descriptions:
        #print(specific_description)
        curr_description = specific_description['cleaned_job_description']
        curr_posting_id = specific_description['posting_id']

        values = []
        sql = "INSERT IGNORE INTO trigrams_postings (trigram, posting_id) VALUES"

        # If the current description is not null
        if curr_description:
            token = nltk.word_tokenize(curr_description)

            # Set up the trigram
            trigram_tokens = ngrams(token, 3)

            # Get all the individual bigrams (tokens)
            fdistunigrams = nltk.FreqDist(trigram_tokens)
            for u,n in fdistunigrams.items():

                # Our current trigram
                temp_trigram = u[0] + " " + u[1] + " " + u[2]
                #print(temp_trigram)

                # If bigram is not in bigram table set raise error
                if not is_in_trigrams(temp_trigram):
                    raise ValueError("Trigram", temp_trigram, "Not in Trigram table")

                values += [temp_trigram, curr_posting_id]
                sql += "(%s, %s),"

            # Convert values to a tuple
            values = tuple(values)
            sql = sql[:-1]
            #print(values)
            #print(sql)
            
            if values:
                cursor.execute(sql,values)

                # Commit as we go in case there is an error
            cursor.execute("COMMIT")

In [ ]:
# Maps bigrams to the unigrams that make them up
def update_trigrams_unigrams():

    # Select the current set of bigrams
    sql = "SELECT trigram FROM trigrams"
    cursor.execute(sql)

    # Get the entire list of dicts
    trigram_list = cursor.fetchall()

    # Iterate over every dict
    for trigram in trigram_list:
        # Get the actual bigram from the dict
        # We need to keep track of the original string since
        # it is the primary key in the bigram table
        curr_trigram = trigram["trigram"]

        # Split the bigram on the space character
        split_trigram = curr_trigram.split(" ")

        # The first word in the trigram
        word_one = split_trigram[0]
        # the second word in the trigram
        word_two = split_trigram[1]
        # the third word in the trigram
        word_three = split_trigram[2]

        # Insert into trigram_unigrams 3 rows, one for each word in the trigram
        sql = """INSERT IGNORE INTO trigrams_unigrams 
                    (trigram, unigram)
                VALUES
                    (%s, %s),
                    (%s, %s),
                    (%s, %s)"""

        # The bigram is curr_bigram, the unigram is the current word
        # This method allows for two rows to be inserted at the same time
        values = (curr_trigram, word_one, 
                  curr_trigram, word_two, 
                  curr_trigram, word_three)
        
        print(curr_trigram)
        #print(values)

        cursor.execute(sql, values)
        cursor.execute("COMMIT")

In [ ]:
update_trigrams()

In [ ]:
update_trigrams_postings()

In [ ]:
update_trigrams_unigrams()

Streaming output truncated to the last 5000 lines.
this job based
this job description
this job duties
this job employee
this job include
this job involves
this job must
this job opening
this job while
this key role
this knowledge seek
this level clearance
this may include
this may not
this person should
this person will
this person would
this position assists
this position based
this position can
this position clicking
this position could
this position excellent
this position experience
this position if
this position is
this position may
this position must
this position offers
this position provides
this position requires
this position responsibilities
this position we
this position what
this position will
this role dedicated
this role falls
this role include
this role is
this role must
this role we
this role will
this role work
this role you
this strategy collaboration
this team also
this team delivers
this team designs
this team you
this vacancy or
this work an
this work is
this wou

# ETC

### Dummygram Functions

In [ ]:
# Compare new data to previous
# New unigrams are inserted
# Old unigrams are updated
def update_dummygrams():
    # Get data descriptions from database
    sql = "SELECT posting_id, cleaned_job_description from postings"
    cursor.execute(sql)
    job_descriptions = cursor.fetchall()
    #print(job_descriptions[0]['job_description'])

    # Collect all the new unigram_data
    unigram_dict = {}

    # Iterate over all job descriptions and collect each unigram with it's frequency
    # Unigram-frequency mapping is in the unigram_dict
    for specific_description in job_descriptions:
        #print(specific_description)
        curr_description = specific_description['cleaned_job_description']

        if curr_description:
            token = nltk.word_tokenize(curr_description)

            fdistunigrams = nltk.FreqDist(token)
            for u in fdistunigrams.items():
                
                temp_word = u[0]
                word_count = u[1]

                if temp_word in unigram_dict:
                    unigram_dict[temp_word] += word_count
                else:
                    unigram_dict[temp_word] = word_count

    # Use fast ngram insert to insert all the new rows very fast
    fast_ngram_insert(unigram_dict, "dummygram", 1000, True)

In [ ]:
update_dummygrams()

In [ ]:
cursor.execute("SELECT * FROM dummygrams")
for x in cursor.fetchall():
    print(x)

In [ ]:
#token = nltk.word_tokenize(open("test.txt","r").read())

sql = "SELECT cleaned_job_description FROM postings"
cursor.execute(sql)

for job_desc in cursor.fetchall():


    print(job_desc)
    token = nltk.word_tokenize(job_desc["cleaned_job_description"])

    bigrams = ngrams(token, 2)
    trigrams = ngrams(token, 3)

    #fdistunigrams = nltk.FreqDist(token)
    fdistbigrams = nltk.FreqDist(bigrams)
    fdisttrigrams = nltk.FreqDist(trigrams)
    if __name__ == '__main__':
        #print(token)
        #print(list(bigrams))

        #print()
        #print("Unigrams")
        #for u in fdistunigrams.items():
        #    print(u)

        print()
        print("Bigrams")
        for k,v in fdistbigrams.items():
            print(k,v)
            print(k[0])
            print(k[1])

        print()
        print("Trigrams")
        for k,v in fdisttrigrams.items():
            print(k,v)

In [ ]:
cursor.execute("SELECT * FROM company_top_ngrams")

for i in cursor.fetchall():
    print(i)